# User Interface (UI) for Analysis


## Installation


Requirements:

- Python 3.10+
- Gradio 5.49.1


In [1]:
# !pip install gradio==5.49.1


## Run the App


### Load Dataset


In [ ]:
import json


def load_dataset(json_path=""):
    with open(json_path, "r", encoding="utf-8") as f:
        return json.load(f)


ANNOTATIONS_DATASET = load_dataset("./dataset.json")


### Helpers


In [3]:
PROMPT_INSTRUCTIONS_PTBR = 'Utilize o texto fornecido entre aspas triplas para extrair informações sensíveis e organize-as em um JSON conforme o formato especificado. Siga as instruções abaixo:\n\nInstruções:\n\n# Diretrizes de Anotação\n\nEste guia descreve o processo de anotação de textos contendo dados pessoais.\n\nO objetivo principal é manter a utilidade do texto, preservando o máximo possível a interpretabilidade, ao mesmo tempo em que se protege a identidade dos indivíduos.\n\n---\n\n## Etapas do Processo de Anotação\n\n1. **Leitura do documento:** leia todo o texto antes de começar a anotar para compreender o contexto geral.\n2. **Identificação de entidades:** identifique todos os tipos de entidades anotáveis e seus respectivos rótulos.\n3. **Mascaramento:** para cada entidade identificada da etapa anterior, avalie se realmente precisa ser mascarada ou não.\n4. **Revisão final:** salve os dados para registrar as anotações e revise para garantir que todas as entidades foram corretamente anotadas e mascaradas.\n\n---\n\n## Definições de Termos\n\nTodo texto contém **Rótulos** e **Entidades**:\n\n- **Rótulos:** categorias semânticas que descrevem o tipo de dado pessoal (ex.: PESSOA, CODIGO, LOCAL).\n  - **Dados Pessoais:** informações que podem identificar direta ou indiretamente um indivíduo.\n  - **Dados Sensíveis:** informações especiais que podem levar a discriminação ou exposição indevida. Demandam maior grau de proteção.\n- **Entidades:** expressões específicas no texto que correspondem a um rótulo (ex.: "Ana Maria" é uma entidade do rótulo PESSOA).\n\n### Dados Pessoais\n\n| Rótulos         | Descrição                                                                                                                                                                         | Entidades                                                                                                        |\n| --------------- | --------------------------------------------------------------------------------------------------------------------------------------------------------------------------------- | ---------------------------------------------------------------------------------------------------------------- |\n| **PESSOA**      | Nomes de pessoas, apelidos, usuário de sistema, iniciais, etc                                                                                                                     | João Silva; joaosilva_sistema; JS.                                                                               |\n| **CODIGO**      | Números e códigos que identificam algo, como CPF, RG, email, URL de rede social, número de telefone, número de passaporte, dados bancários, placa de veículo, número de processos | 123.456.789-00 (CPF); exemplo@mail.com; https://instagram.com/usuario; +55 11 91234-5678; BR1234567 (passaporte) |\n| **LOCAL**       | Lugares e localizações, como:<br>• Cidades, áreas, países etc.<br>• Endereços<br>• Infraestruturas nomeadas (pontos de ônibus, pontes etc.)                                       | São Paulo; Avenida Paulista, 1000; Parque Ibirapuera; Brasil                                                     |\n| **DEMOGRAFICO** | Atributo demográfico de uma pessoa, como:<br>• Profissão, escolaridade, formação acadêmica <br>• Estado Civil, patentes                                                           | Advogado; Ensino Superior; Bacharel em Direito; Solteiro                                                         |\n| **DATAHORA**    | Descrição de uma data específica (ex.: 3 de outubro de 2018), hora (ex.: 9h48) ou duração (ex.: 18 anos).                                                                         | 3 de outubro de 2018; 09:48; 18 anos; 01/01/2020                                                                 |\n| **QUANTIDADE**  | Descrição de uma quantidade significativa, ex.: percentuais ou valores monetários.                                                                                                | 50%; R$ 1.000,00; 1.000 pessoas                                                                                  |\n| **OUTROS**      | Todo outro tipo de informação que descreve um indivíduo e que não se enquadra nas categorias acima.                                                                               | SAMSUNG SM-J701F; ESCORYY 53/2000;                                                                               |\n\n\n### Dados Sensíveis\n\n| Rótulos      | Descrição                                                                                                                                                               | Entidades                                                       |\n| ------------ | ----------------------------------------------------------------------------------------------------------------------------------------------------------------------- | --------------------------------------------------------------- |\n| **RELIGIAO** | Crenças religiosas ou filosóficas                                                                                                                                       | católico, evangélico, ateu                                      |\n| **POLITICA** | Opiniões políticas, filiação sindical                                                                                                                                   | filiação partidária, participação em protestos                  |\n| **GENERO**   | Orientação sexual ou vida sexual                                                                                                                                        | heterossexual, homossexual, M (masculino)                       |\n| **ORIGEM**   | Origem racial ou étnica. Idioma nativo, descendência, herança. Ex: preto, pardo                                                                                         | preto, pardo, indígena                                          |\n| **SAUDE**    | Dados de saúde, genéticos e biométricos. Descrições físicas, diagnósticos, marcas de nascença. Inclui hábitos sensíveis relacionados à saúde, como abuso de substâncias | diabetes, HIV, CID 10 I, FLUDROCORTISONA, 45 Kg, 1,58 de altura |\n\n\n---\n\n# Observações Importantes\n\n**Regras Gerais**\n\n- **CPF e RG**: sempre anotar, independentemente do contexto.\n- Em caso de dúvida se deve anotar algo, **anote**, pois priorizamos o **sigilo frente à utilidade**.\n\n## ANOTAR\n\n- **Assinatura com CPF ou RG:** além do **CPF/RG**, anotar **PESSOA correspondente ao CPF/RG**.\n- **Erros ortográficos em entidades:** anotar mesmo assim, pois mantém a integridade dos dados (Exemplo: CPF incompleto: 023.512.355-1).\n- **Números de documentos externos (CODIGO)** (ex.: `0001234-56.2020.8.26.2330`) ou **outros códigos únicos** que possam identificar pessoas em outro documento externo.\n- **DATAHORA** e **QUANTIDADE** **somente** se contribuírem para **identificação do indivíduo**.\n\n---\n\n## NÃO ANOTAR\n\n### Dados e informações gerais\n\n- **Números de processos judiciais**: número do próprio documento.\n- **Assinaturas de documentos** (inclusive certificado digital).\n- **Códigos e URLs** usados apenas para validar documentos.\n- **Valores e Quantidades de causa** em processos judiciais (Rótulos **QUANTIDADE** e **DATAHORA**), por exemplo: quanto que um advogado está pedindo em um processo.\n- **Termos "maior" ou "menor"**, por indicam idade (criança/adolescente) e ajuda a destacar o documento se o próprio se refere a menos.\n- **Pronomes** que indiquem sexo (ex.: "ele", "ela", "dela").\n- **Matrículas** de servidores públicos (Exemplo: número SIAPE).\n- **Registros profissionais**, como OAB, CREA etc.\n- **Nacionalidade** (ex.: "brasileiro", "argentino") - mesmo se associada a pessoa.\n- **Nomes de autoridades públicas.**\n\n### Pessoas e autoridades públicas\n\n- **Dados institucionais** de órgãos públicos (endereços, e-mails, telefones, CEPs).\n\n  - _Exceção:_ se o dado for **pessoal** (CPF, telefone pessoal, estado civil) da pessoa física relacionada à instituição.\n\n- **Dados de pessoas jurídicas (CNPJ)** ou informações profissionais de autoridades públicas.\n\n  - _Exceção:_ se o dado for **pessoal** (CPF, telefone pessoal, estado civil) da pessoa física relacionada à instituição.\n\n'
PROMPT_INSTRUCTIONS_EN = "Use the text provided between triple quotes to extract sensitive information and organize it into a JSON according to the specified format. Follow the instructions below:\n\n**Annotation Guidelines**\n\nThis guide describes the process of annotating texts containing personal data.\n\nThe main goal is to preserve as much interpretability as possible while protecting individuals' identities.\n\n---\n\n## **Annotation Process Steps**\n\n1. **Read the document:** Read the entire text before annotating to understand the overall context.\n2. **Identify entities:** Identify all annotatable entity types and their respective labels.\n3. **Masking:** For each identified entity, evaluate whether it truly needs to be masked.\n4. **Final review:** Save the data to record the annotations and review to ensure all entities were correctly annotated and masked.\n\n---\n\n## **Term Definitions**\n\nEvery text contains **Labels** and **Entities**:\n\n- **Labels:** semantic categories that describe the type of personal data (e.g., PERSON, CODE, LOCATION).\n\n  - **Personal Data:** information that can directly or indirectly identify an individual.\n  - **Sensitive Data:** special information that may lead to discrimination or undue exposure and requires greater protection.\n\n- **Entities:** specific expressions in the text that correspond to a label (e.g., “Ana Maria” is an entity under PERSON).\n\n| Labels          | Description                                                                                                                                               | Entities                                                                                                                                                                   |\n| --------------- | --------------------------------------------------------------------------------------------------------------------------------------------------------- | -------------------------------------------------------------------------------------------------------------------------------------------------------------------------- |\n| **PERSON**      | Names of people, nicknames, system usernames, initials, etc.                                                                                              | João Silva; joaosilva_sistema; JS.                                                                                                                                         |\n| **CODE**        | Numbers and codes that identify something, such as CPF, RG, email, social media URL, phone number, passport number, bank data, vehicle plate, case number | 123.456.789-00 (CPF); [exemplo@mail.com](mailto:exemplo@mail.com); [https://instagram.com/usuario](https://instagram.com/usuario); +55 11 91234-5678; BR1234567 (passport) |\n| **LOCATION**    | Places and locations, such as:<br>• Cities, areas, countries, etc.<br>• Addresses<br>• Named infrastructures (bus stops, bridges, etc.)                   | São Paulo; Avenida Paulista, 1000; Parque Ibirapuera; Brasil                                                                                                               |\n| **DEMOGRAPHIC** | A person’s demographic attribute, such as:<br>• Profession, education, academic background<br>• Marital status, rankings                                  | Lawyer; Higher Education; Bachelor of Law; Single                                                                                                                          |\n| **DATETIME**    | Description of a specific date (e.g., October 3, 2018), time (e.g., 9:48 AM), or duration (e.g., 18 years).                                               | October 3, 2018; 09:48; 18 years; 01/01/2020                                                                                                                               |\n| **QUANTITY**    | Description of a significant amount, e.g., percentages or monetary values.                                                                                | 50%; R$ 1,000.00; 1,000 people                                                                                                                                             |\n| **OTHERS**      | Any other type of information that describes an individual and does not fit the categories above.                                                         | SAMSUNG SM-J701F; ESCORYY 53/2000                                                                                                                                          |\n\n\n| Labels       | Description                                                                                                                                          | Entities                                                       |\n| ------------ | ---------------------------------------------------------------------------------------------------------------------------------------------------- | -------------------------------------------------------------- |\n| **RELIGION** | Religious or philosophical beliefs                                                                                                                   | Catholic, evangelical, atheist                                 |\n| **POLITICS** | Political opinions, union affiliation                                                                                                                | party affiliation, participation in protests                   |\n| **GENDER**   | Sexual orientation or sexual life                                                                                                                    | heterosexual, homosexual, M (male)                             |\n| **ORIGIN**   | Racial or ethnic origin. Native language, ancestry, heritage. Example: Black, Brown                                                                  | Black, Brown, Indigenous                                       |\n| **HEALTH**   | Health, genetic, and biometric data. Physical descriptions, diagnoses, birthmarks. Includes sensitive health-related habits, such as substance abuse | diabetes, HIV, ICD 10 I, FLUDROCORTISONE, 45 kg, 1.58 m height |\n\n\n---\n\n# **Important Observations**\n\n## **General Rules**\n\n- **CPF and RG:** always annotate them, regardless of context.\n- When in doubt about annotating something, **annotate it**, because we prioritize **privacy over utility**.\n\n---\n\n## **ANNOTATE**\n\n- **Signature with CPF or RG:** besides the **CPF/RG**, annotate the **PERSON associated with the CPF/RG**.\n- **Spelling errors in entities:** annotate anyway to maintain data integrity (Example: incomplete CPF: 023.512.355-1).\n- **External document numbers (CODE)** (e.g., _0001234-56.2020.8.26.2330_) or **other unique codes** that can identify people in another external document.\n- **DATETIME** and **QUANTITY** only if they contribute to **identifying the individual**.\n\n---\n\n## **DO NOT ANNOTATE**\n\n### **General data and information**\n\n- **Court case numbers:** number of the document itself.\n- **Document signatures** (including digital certificates).\n- **Codes and URLs** used only to validate documents.\n- **Case values or quantities** in court processes (**QUANTITY** and **DATETIME** labels), e.g., how much a lawyer is requesting in a lawsuit.\n- Terms like **“adult” or “minor”**, as they indicate age but do not identify the person.\n- **Pronouns** indicating gender (e.g., “he,” “she,” “hers”).\n- **Registration numbers** of public servants (e.g., SIAPE number).\n- **Professional records**, such as OAB, CREA, etc.\n- **Nationality** (e.g., Brazilian, Argentine) — even when linked to a person.\n- **Names of public authorities.**\n\n### **People and public authorities**\n\n- **Institutional data** of public agencies (addresses, emails, phones, ZIP codes).\n\n  - _Exception:_ if the data is **personal** (CPF, personal phone number, marital status) of an individual associated with the institution.\n\n- **Legal entity data (CNPJ)** or professional information of public authorities.\n\n  - _Exception:_ if the information is **personal** (CPF, personal phone number, marital status) of an individual.\n\n"

### Default Configurations


In [4]:
color_map = {
    "PESSOA": "#FFB3BA",
    "CODIGO": "#BAE1FF",
    "LOCAL": "#BFFFB3",
    "DEMOGRAFICO": "#FFFFBA",
    "DATAHORA": "#FFDFBA",
    "QUANTIDADE": "#B3FFD9",
    "OUTROS": "#E2BAFF",
    "RELIGIAO": "#BAFFC9",
    "POLITICA": "#FFD6BA",
    "GENERO": "#FFBAED",
    "ORIGEM": "#BAFFF2",
    "SAUDE": "#FFC9BA",
}

HighlightedTextParams = {
    "color_map": color_map,
    "combine_adjacent": True,
    "show_legend": True,
    "render": False,
}


### Show UI


In [6]:
import gradio as gr

# ---------------------------------------------------------
# Utility Functions
# ---------------------------------------------------------


def build_dropdown_choices(dataset):
    """
    Build formatted dropdown choices:
    - Label: "ID — truncated_content"
    - Value: full content (passed to the app)
    """
    choices = []
    for d in dataset:
        _id = d.get("id", "")
        content = d.get("conteudo", "")
        label = f"{_id} — {content}"
        choices.append((label, content))

    return choices


def build_description_model(record, model_name, ndigits=2):
    """
    Build formatted precision / recall / F1 description for a given model.
    """
    return f"""
- Precision: **{round(record.get(f"score_{model_name}_precision", 0), ndigits)}**  
- Recall: **{round(record.get(f"score_{model_name}_recall", 0), ndigits)}**  
- F1: **{round(record.get(f"score_{model_name}_f1", 0), ndigits)}**
- Runtime: **{round(record.get(f"anotacao_{model_name}_time", 0) / 1000, ndigits)}**
"""


def validar_estatico(content, ndigits=2):
    """
    Given a text, find its annotations in ANNOTATIONS_DATASET
    and return:
        - HighlightedText values for GT, GPT, Gemini, Claude, Sabia
        - Markdown metric descriptions for all models
    """
    for record in ANNOTATIONS_DATASET:
        if record.get("conteudo") == content:
            # ---------------- Highlighted Text ----------------
            hl_gt_val = {"text": content, "entities": record.get("anotacao", [])}
            hl_gpt_val = {
                "text": content,
                "entities": record.get("anotacao_openai", []),
            }
            hl_gemini_val = {
                "text": content,
                "entities": record.get("anotacao_gemini", []),
            }
            hl_claude_val = {
                "text": content,
                "entities": record.get("anotacao_claude", []),
            }
            hl_sabia_val = {
                "text": content,
                "entities": record.get("anotacao_maritaca", []),
            }

            # ---------------- Metrics (Markdown) ----------------
            md_gt_text = f"""
- Title: **{record.get("id", "")[:100]}...**
- Entities Count: **{len(record.get("anotacao", []))}**  
- Words Count: **{len(content.split())}**  
- Characters Count: **{len(content)}**
"""

            md_gpt_text = build_description_model(record, "openai", ndigits)
            md_gemini_text = build_description_model(record, "gemini", ndigits)
            md_claude_text = build_description_model(record, "claude", ndigits)
            md_sabia_text = build_description_model(record, "maritaca", ndigits)

            return (
                hl_gt_val,
                hl_gpt_val,
                hl_gemini_val,
                hl_claude_val,
                hl_sabia_val,
                md_gt_text,
                md_gpt_text,
                md_gemini_text,
                md_claude_text,
                md_sabia_text,
            )

    # If content not found, return empty values
    return ({}, {}, {}, {}, {}, "", "", "", "", "")


# ---------------------------------------------------------
# Gradio UI Components
# ---------------------------------------------------------

# Dropdown of formatted examples
choices_dropdown = build_dropdown_choices(ANNOTATIONS_DATASET)

dropdown_examples = gr.Dropdown(
    label="Examples (Title — Content)",
    choices=choices_dropdown,
    value=choices_dropdown[0][1],  # ⬅ Seleciona automaticamente o conteúdo da 1ª opção
    interactive=True,
    render=False,
)

# Main text input
initial_text = choices_dropdown[0][1]
txt_input = gr.Textbox(
    value=initial_text,
    label="Content",
    lines=12,
    show_copy_button=True,
    render=False,
    interactive=False,
    visible=False,
)

# Highlighted annotations for each model
hl_gt = gr.HighlightedText(label="Ground Truth", **HighlightedTextParams)
hl_gpt = gr.HighlightedText(label="GPT", **HighlightedTextParams)
hl_gemini = gr.HighlightedText(label="GEMINI", **HighlightedTextParams)
hl_claude = gr.HighlightedText(label="CLAUDE", **HighlightedTextParams)
hl_sabia = gr.HighlightedText(label="SABIA", **HighlightedTextParams)

# Markdown metric panels
md_gt = gr.Markdown(label="Ground Truth")
md_gpt = gr.Markdown(label="GPT")
md_gemini = gr.Markdown(label="GEMINI")
md_claude = gr.Markdown(label="CLAUDE")
md_sabia = gr.Markdown(label="SABIA")

# Optional: raw model response
txt_response = gr.Textbox(
    label="Original Response",
    lines=12,
    show_copy_button=True,
    render=False,
)


# ---------------------------------------------------------
# Gradio App Layout
# ---------------------------------------------------------

with gr.Blocks(
    title="Results Analysis",
    js="() => {document.body.classList.remove('dark')}",
) as demo:
    gr.HTML("<h1>Results Analysis</h1>")

    with gr.Tab("Introduction"):
        md_intro = gr.Markdown(
            """
            This tool allows you to explore the annotation results and metrics for different models on a dataset of legal texts related to the LGPD (Brazilian General Data Protection Law).
            
            We also provide the prompt instructions used for annotating the texts, both in English and Portuguese (PT-BR).

            This is part of the supplementary material for the paper **"LGPD Benchmark: A Legal Text Corpus for Evaluating Personal Data Pseudonymization in Brazilian Portuguese"**
           """,
        )

    with gr.Tab("Comparison"):
        gr.HTML("<h2>Model Annotations Comparison</h2>")
        gr.Markdown(
            """
            Select an example from the dropdown to load its content and view the annotations
            and metrics for different models.
            """
        )
        # Dropdown with custom preview
        with gr.Row():
            dropdown_examples.render()

        # Text that loads the selected example
        with gr.Row():
            txt_input.render()

        # Highlighted annotations + metrics in columns
        with gr.Row():
            with gr.Column():
                md_gt.render()
                hl_gt.render()

            with gr.Column():
                md_gpt.render()
                hl_gpt.render()

            with gr.Column():
                md_gemini.render()
                hl_gemini.render()

            with gr.Column():
                md_claude.render()
                hl_claude.render()

            with gr.Column():
                md_sabia.render()
                hl_sabia.render()

    with gr.Tab("Prompt Instructions"):
        md_prompt = gr.Markdown(PROMPT_INSTRUCTIONS_EN)

    with gr.Tab("Prompt Instructions (PT-BR)"):
        md_prompt = gr.Markdown(PROMPT_INSTRUCTIONS_PTBR)

    # --- When dropdown changes, update text ---
    dropdown_examples.change(
        inputs=[dropdown_examples],
        fn=lambda content: content,  # returns full content
        outputs=[txt_input],
    )

    # --- When text changes (triggered by dropdown), compute annotations ---
    txt_input.change(
        inputs=[txt_input],
        fn=validar_estatico,
        outputs=[
            hl_gt,
            hl_gpt,
            hl_gemini,
            hl_claude,
            hl_sabia,
            md_gt,
            md_gpt,
            md_gemini,
            md_claude,
            md_sabia,
        ],
    )

    demo.load(
        fn=validar_estatico,
        inputs=[txt_input],
        outputs=[
            hl_gt,
            hl_gpt,
            hl_gemini,
            hl_claude,
            hl_sabia,
            md_gt,
            md_gpt,
            md_gemini,
            md_claude,
            md_sabia,
        ],
    )


# Launch
demo.launch(
    inbrowser=True,
)


* Running on local URL:  http://127.0.0.1:7861
* To create a public link, set `share=True` in `launch()`.
